In [212]:
from operator import index
from tkinter import N
from Bio import Entrez
import requests
import pandas as pd
import json
from urllib.error import HTTPError

In [213]:
# Open the file with the organism's names
path = 'array-organismi.txt'
with open(path, 'r') as file:
    organisms_names = [x for x in file.readline().split("'") if x!=", " if x!='[' if x!=']'] 
print(organisms_names)
file.close()

['Homo sapiens', 'Mus musculus', 'Rattus norvegicus', 'Saccharomyces cerevisiae S288C', 'Sus scrofa', 'Pseudomonas aeruginosa PAO1', 'Danio rerio', 'Drosophila melanogaster', 'Listeria monocytogenes EGD-e', 'Erwinia amylovora CFBP1430', 'Arabidopsis thaliana', 'Xenopus laevis', 'Bos taurus', 'Ovis aries', 'Gallus gallus', 'Mustela putorius furo', 'Oryctolagus cuniculus', 'Macaca mulatta', 'Canis lupus familiaris', 'Schizosaccharomyces pombe', 'Caenorhabditis elegans', 'Dictyostelium discoideum AX4', 'Cavia porcellus', 'Bacteroides eggerthii', 'Candida albicans SC5314', 'Thalassiosira pseudonana CCMP1335', 'Anopheles gambiae str. PEST', 'Pan troglodytes', 'Xenopus tropicalis', 'Parabacteroides johnsonii', 'Eremothecium gossypii ATCC 10895', 'Theileria annulata', 'Theileria parva strain Muguga', 'Cryptosporidium hominis TU502', 'Cryptosporidium parvum Iowa II', 'Mesocricetus auratus', 'Entamoeba histolytica HM-1:IMSS', 'Neurospora crassa OR74A', 'Micromonas pusilla CCMP1545', 'Volvox car

In [56]:
len(organisms_names) # we have this number of organims

845

In [57]:
organismo = organisms_names[0]
organismo

'Homo sapiens'

In [214]:
# Cercare la lista di articoli che parlano di un organismo
# Input: nome di un organismo 
# Output: Lista di articoli (PubMed Id) che parlano di questo organismo

def OrganismoArticoli(nomeOrganismo, geneOrganismo):
    ### lista id articoli per organismo
    articleOrganismo_list = []
    # for organismo in set(nomeOrganismo_list): ## tolgo eventuali doppioni da nomeOrganismo_list
    try:
        handleGene = Entrez.esearch(db='pubmed', retmax=10, term="{0} AND {1}".format(nomeOrganismo, geneOrganismo)) #solo si cercarno 10 articoli
    except HTTPError as err:
        if err.code == 404:
            print('error 404 detectado')
        else:
            print('error detectado')
            raise
            
    articleOrganismo = Entrez.read(handleGene, validate=True)['IdList']
    articleOrganismo_list.append(articleOrganismo) ## è una lista di tante liste quanti sono gli organismi
    return articleOrganismo_list[0]


geneOrganismo = 'CFTR'
nomeOrganismo = 'Homo Sapiens'
OrganismoArticoli(nomeOrganismo, geneOrganismo)

C:\Users\ennio\AppData\Local\Programs\Python\Python38-32\lib\site-packages\Bio\Entrez\__init__.py:658: UserWarning: 
Email address is not specified.

To make use of NCBI's E-utilities, NCBI requires you to specify your
email address with each request.  As an example, if your email address
is A.N.Other@example.com, you can specify it as follows:
   from Bio import Entrez
   Entrez.email = 'A.N.Other@example.com'
In case of excessive usage of the E-utilities, NCBI will attempt to contact
a user at the email address provided before blocking access to the
E-utilities.
  warnings.warn(


['35655004', '35646184', '35641986', '35627829', '35627274', '35626748', '35624092', '35592521', '35576754', '35568033']

In [215]:
# Input: 
#     dfOrganisms - create df where to save the articles
#     organisms_names - an array of organisms
# Output: Dataframe with one Organism, the 
# Takes the Organisms list and search the list of articles for each organism




def organismArticles(organisms_names):
    dfOrganisms = pd.DataFrame(columns = ["Organismo", "Articulos", "No_articulos"])
    geneOrganismo = 'CFTR'

    individualPaperOrgn = OrganismoArticoli(organisms_names, geneOrganismo)
    new_row = {'Organismo':organisms_names, 'Articulos': individualPaperOrgn, 'No_articulos': len(individualPaperOrgn)}
#     dfOrganisms = dfOrganisms.append(new_row, ignore_index=True)
    
    return new_row
    
#     j = 0
#     for org in organisms_names:
#         individualPaperOrgn = OrganismoArticoli(org, geneOrganismo)
#         new_row = {'Organismo':org, 'Articulos': individualPaperOrgn, 'No_articulos': len(individualPaperOrgn)}
# #         print(new_row)
#         dfOrganisms = dfOrganisms.append(new_row, ignore_index=True)
#         j = j+1
#         if j>3:
#             break
    
#     return dfOrganisms



dfArticlesNumbers = organismArticles(organisms_names[0])
print(dfArticlesNumbers)


{'Organismo': 'Homo sapiens', 'Articulos': ['35655004', '35646184', '35641986', '35627829', '35627274', '35626748', '35624092', '35592521', '35576754', '35568033'], 'No_articulos': 10}


In [216]:
# Input: id di un articolo
# Output: json con con parole classificate
def query_pmid(pmids, url="http://bern2.korea.ac.kr/pubmed"):
    return requests.get(url + "/" + ",".join(pmids)).json()

print(query_pmid('5723213'))

[{'_id': '5', 'annotations': [{'id': ['CUI-less'], 'is_neural_normalized': False, 'mention': 'myohemerythrin', 'obj': 'gene', 'prob': 0.973336935043335, 'span': {'begin': 47, 'end': 61}}, {'id': ['CUI-less'], 'is_neural_normalized': False, 'mention': 'hemerythrin', 'obj': 'gene', 'prob': 0.9804603457450867, 'span': {'begin': 66, 'end': 77}}], 'pmid': '5', 'text': 'Atomic models for the polypeptide backbones of myohemerythrin and hemerythrin.'}, {'_id': '7', 'annotations': [{'id': ['CHEBI:58097'], 'is_neural_normalized': False, 'mention': 'morphine', 'obj': 'drug', 'prob': 0.9975878000259399, 'span': {'begin': 50, 'end': 58}}], 'pmid': '7', 'text': 'Maturation of the adrenal medulla--IV. Effects of morphine.'}, {'_id': '2', 'annotations': [{'id': ['CHEBI:36980'], 'is_neural_normalized': False, 'mention': 'pyridine nucleotide', 'obj': 'drug', 'prob': 0.9964399337768555, 'span': {'begin': 68, 'end': 87}}], 'pmid': '2', 'text': 'Delineation of the intimate details of the backbone conformat

In [61]:
query_pmid(['35513433'])

[{'_id': '35513433',
  'annotations': [{'id': ['CHEBI:30120'],
    'is_neural_normalized': False,
    'mention': 'Cl(-)',
    'obj': 'drug',
    'prob': 0.9997637867927551,
    'span': {'begin': 24, 'end': 29}},
   {'id': ['CL:0000775'],
    'is_neural_normalized': False,
    'mention': 'neutrophil',
    'obj': 'cell_type',
    'prob': 0.8723117113113403,
    'span': {'begin': 53, 'end': 63}},
   {'id': ['mim:108725', 'mesh:D050197'],
    'is_neural_normalized': True,
    'mention': 'atherosclerotic cardiovascular diseases',
    'obj': 'disease',
    'prob': 0.9999982714653015,
    'span': {'begin': 138, 'end': 177}},
   {'id': ['mesh:D054058'],
    'is_neural_normalized': False,
    'mention': 'acute coronary syndrome',
    'obj': 'disease',
    'prob': 0.9999878406524658,
    'span': {'begin': 186, 'end': 209}},
   {'id': ['mesh:D054058'],
    'is_neural_normalized': False,
    'mention': 'ACS',
    'obj': 'disease',
    'prob': 0.999940037727356,
    'span': {'begin': 211, 'end': 21

In [217]:
def extractEntities(articleId):
    dataEntities = query_pmid([articleId])

    entityWord_List = []
    entityClass_List = []
#     print('articulo ', articleId)
#     print(dataEntities)

    for n in range(0, len(dataEntities[0]['annotations'])):
#         print(dataEntities[0]['annotations'][n]['prob'])
#         print(dataEntities[0]['annotations'][n]['mention'])
        if 'prob' in dataEntities[0]['annotations'][n]:
            if dataEntities[0]['annotations'][n]['prob'] != None:
                if dataEntities[0]['annotations'][n]['prob']>0.9 and len(dataEntities[0]['annotations'][n]['mention'])>2:
                    entityWord_List.append(dataEntities[0]['annotations'][n]['mention'])
                    entityClass_List.append(dataEntities[0]['annotations'][n]['obj'])
            else:
                print('{0}, del articulo {1} detectado con Prob: None'.format(dataEntities[0]['annotations'][n]['mention'], articleId))
    
        else:
            print('se detecto entidad sin probabilidad de articulo {0}'.format(articleId))
    return(entityWord_List, entityClass_List )

In [229]:
pd.set_option('display.max_rows', None)

def singleArticleEntities(article_number, oganismArticle):
    
    entity_list, class_list = extractEntities(article_number)
    
    SingleTermsOrganismsDF = pd.DataFrame(columns = ["StartNode", "EndNode", "Class", "Weight", "Rank"]) # rank - similarity to the polmonary tissue
#     print(entity_list)

    for i in range(0, len(entity_list)):
        singleNewRow = { "StartNode": oganismArticle.lower(), "EndNode": entity_list[i].lower(), "Class": 'species', "Weight":1, "Rank":0} # 
        SingleTermsOrganismsDF = SingleTermsOrganismsDF.append(singleNewRow, ignore_index=True)
#         print(entity_list[i].lower())
        for j in range(0, len(entity_list)):
            if i!=j:
                singleNewRow = { "StartNode": entity_list[i].lower(), "EndNode": entity_list[j].lower(), "Class": class_list[i], "Weight":1, "Rank":0} # la clase del StartNode
                SingleTermsOrganismsDF = SingleTermsOrganismsDF.append(singleNewRow, ignore_index=True)
    SingleTermsOrganismsDF = SingleTermsOrganismsDF.groupby(['StartNode', 'EndNode', 'Class', 'Rank' ], as_index=False)['Weight'].sum()

    return SingleTermsOrganismsDF



# prueba = {'Organismo': 'Mus musculus', 'Articulos': ['35635440', '35563597', '35513433', '35484438', '35449374', '35417692', '35413967', '35411814', '35402186', '35392567'], 'No_articulos': 10}

# singleArticleEntities(prueba['Articulos'][0], prueba['Organismo'])



In [225]:
a = singleArticleEntities('35513433', 'Mus musculus')
print(a[1])
a[0]

['Cl(-)', 'atherosclerotic cardiovascular diseases', 'acute coronary syndrome', 'ACS', 'oxidized low-density lipoprotein', 'oxLDL', 'Cl(-)', 'Cl(-)', 'cystic fibrosis', 'cystic fibrosis transmembrane conductance regulator', 'CFTR', 'Cl(-)', 'Cl(-)', 'CFTR', 'Cftr(-/-)', 'mice', 'CFTR', 'CFTR(inh)-172', 'mice', 'OxLDL', 'CFTR', 'Cl(-)', 'Cl(-)', 'CFTR(inh)-172', 'CFTR', 'SGK1', 'oxygen', 'oxLDL', 'atherosclerotic', 'mice', 'stable angina', 'ST-elevation ACS', 'STE-ACS', 'patients', 'Cl(-)', 'SGK1', 'CFTR', 'CFTR', 'oxLDL', 'mice', 'atherosclerotic', 'mice', 'patients', 'STE-ACS', 'Cl(-)', 'Cl(-)', 'atherosclerosis', 'ACS', 'Cl(', 'SGK1', 'CFTR', 'atherosclerotic cardiovascular diseases']


StartNode  \
0                                                  acs   
1                                                  acs   
2                                                  acs   
3                                                  acs   
4                                                  acs   
5                                                  acs   
6                                                  acs   
7                                                  acs   
8                                                  acs   
9                                                  acs   
10                                                 acs   
11                                                 acs   
12                                                 acs   
13                                                 acs   
14                                                 acs   
15                                                 acs   
16                                                 acs   
17                                                 acs   
18                                                 acs   
19                                                 acs   
20                                                 acs   
21                             acute coronary syndrome   
22                             acute coronary syndrome   
23                             acute coronary syndrome   
24                             acute coronary syndrome   
25                             acute coronary syndrome   
26                             acute coronary syndrome   
27                             acute coronary syndrome   
28                             acute coronary syndrome   
29                             acute coronary syndrome   
30                             acute coronary syndrome   
31                             acute coronary syndrome   
32                             acute coronary syndrome   
33                             acute coronary syndrome   
34                             acute coronary syndrome   
35                             acute coronary syndrome   
36                             acute coronary syndrome   
37                             acute coronary syndrome   
38                             acute coronary syndrome   
39                             acute coronary syndrome   
40                             acute coronary syndrome   
41                                     atherosclerosis   
42                                     atherosclerosis   
43                                     atherosclerosis   
44                                     atherosclerosis   
45                                     atherosclerosis   
46                                     atherosclerosis   
47                                     atherosclerosis   
48                                     atherosclerosis   
49                                     atherosclerosis   
50                                     atherosclerosis   
51                                     atherosclerosis   
52                                     atherosclerosis   
53                                     atherosclerosis   
54                                     atherosclerosis   
55                                     atherosclerosis   
56                                     atherosclerosis   
57                                     atherosclerosis   
58                                     atherosclerosis   
59                                     atherosclerosis   
60                                     atherosclerosis   
61                                     atherosclerotic   
62                                     atherosclerotic   
63                                     atherosclerotic   
64                                     atherosclerotic   
65                                     atherosclerotic   
66                                     atherosclerotic   
67                                     atherosclerotic   
68                                     athe

In [226]:
len(a[1])

52

In [233]:
# From a list of articles makes a dataframe with the connections to make the graph then

# input: dic with node organism | list of articles | number of articles 
# output: dataframe with the articles words to makes the graphs

prueba = {'Organismo': 'Mus musculus', 'Articulos': ['35635440', '35563597', '35513433', '35484438', '35449374', '35417692', '35413967', '35411814', '35402186', '35392567'], 'No_articulos': 10}



def ArticlesToDF(organism_data):
    generalDF = pd.DataFrame(columns = ["StartNode", "EndNode", "Class", "Weight", "Rank"])
    i = 0
    for artcl in organism_data['Articulos']:
        tempData = singleArticleEntities(artcl, organism_data['Organismo'])
#         print(tempData)
        generalDF = pd.concat([tempData, generalDF], axis=0)
    
#         From organisms to entities
        
    
    
#         i=i+1
#         if i==3: # Se toman los primeros tres articulos solo como prueba piloto
#             break
    
    generalDF = generalDF.reset_index().drop(columns = ['index']).groupby(['StartNode', 'EndNode', 'Class', 'Rank' ], as_index=False)['Weight'].sum()
    
    return generalDF

ArticlesToDF(prueba)
    


p.Trp401X, del articulo 35392567 detectado con Prob: None


StartNode  \
0                                         16s rrna gene   
1                                         16s rrna gene   
2                                         16s rrna gene   
3                                         16s rrna gene   
4                                         16s rrna gene   
5                                         16s rrna gene   
6                                         16s rrna gene   
7                                         16s rrna gene   
8                                         16s rrna gene   
9                                         16s rrna gene   
10                                        16s rrna gene   
11    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
12    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
13    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
14    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
15    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
16    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
17    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
18    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
19    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
20    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
21    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
22    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
23    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
24    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
25    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
26    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
27    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
28    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
29    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
30    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
31    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
32    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
33    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
34    3-(4,5)-dimethylthiahiazo (-z-y1)-3,5-di-pheny...   
35           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
36           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
37           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
38           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
39           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
40           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
41           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
42           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
43           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
44           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
45           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
46           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
47           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
48           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
49           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
50           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
51           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
52           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
53           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
54           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
55           7-(3,4-dimethoxyphenyl)-n-(4-ethoxyphenyl)   
56                              achaete-scute homolog 3   
57                              achaete-scute homolog 3   
58                              achaete-scute homolog 3   
59                              achaete-scute homolog 3   
60                              achaete-scute homolog 3   
61                              achaete-scute homolog 3   
62                              achaete-scute homolog 3   
63                              achaete-scute homolog 3   
64                              achaete-scute homolog 3   
65                              achaete-scute homolog 3   
66                              achaete-scute homolog 3   
67                              ac

In [237]:

def totalArticles(organisms_names):
    
#     dfArticlesNumbers = organismArticles(organisms_names)
    OrgNoArtcls = 0 
    OrgArtcls  = 0 
    dfTotal = pd.DataFrame(columns = ["StartNode", "EndNode", "Class", "Weight", "Rank"])
    
#     pd.DataFrame() # DF that contains all the organisms, with the articles and processed with NER
    orgnNoIncluded = []
    orgnIncluded = []
    k =0
    
    for organism in organisms_names:
        
        newRow = { "StartNode": 'cftr', "EndNode": organism.lower(), "Class": 'gene', "Weight":1, "Rank":0}
        dfTotal = dfTotal.append(newRow, ignore_index=True)
        
        
        row = organismArticles(organism)
        k=k+1
        if k>6:
            break
        
        print('\n',row)
        if row['No_articulos'] != 0:
            tempData = ArticlesToDF(row)
            dfTotal = pd.concat([tempData, dfTotal], axis=0)
            OrgArtcls=OrgArtcls+1
            orgnIncluded.append(organism)
            print(OrgArtcls)
            print(row['Organismo'])
        else:
            orgnNoIncluded.append(organism)
            OrgNoArtcls=OrgNoArtcls+1

        
    
#     for index, row in dfArticlesNumbers.iterrows():
# #         print(row['Organismo'])
#         print('\n',row)
#         if row['No_articulos'] != 0:
#             tempData = ArticlesToDF(row)
#             dfTotal = pd.concat([tempData, dfTotal], axis=0)
#             OrgArtcls=OrgArtcls+1
#             print(OrgArtcls)
#             print(row['Organismo'])
#         else:
#             OrgNoArtcls=OrgNoArtcls+1
#             print(row)
#             print(index, row['Organismo'], row['Articulos'], row['No_articulos'])    
    
    print('Hay {0} organismos con articulos y {1} organismos sin articulos '.format( len(orgnIncluded), len(orgnNoIncluded)))
    return dfTotal.reset_index().drop(columns = ['index']),orgnIncluded, orgnNoIncluded
    
dataFinal, Organismos_incluidos, Organismos_no_incluidos   = totalArticles(organisms_names)


 {'Organismo': 'Homo sapiens', 'Articulos': ['35655004', '35646184', '35641986', '35627829', '35627274', '35626748', '35624092', '35592521', '35576754', '35568033'], 'No_articulos': 10}
M470V, del articulo 35646184 detectado con Prob: None
 G542X, del articulo 35646184 detectado con Prob: None
G542X, del articulo 35646184 detectado con Prob: None
W1282X, del articulo 35646184 detectado con Prob: None
N1303K, del articulo 35646184 detectado con Prob: None
R117H, del articulo 35646184 detectado con Prob: None
W1282X, del articulo 35646184 detectado con Prob: None
mutations, del articulo 35641986 detectado con Prob: None
W1282X, del articulo 35624092 detectado con Prob: None
W1282X, del articulo 35624092 detectado con Prob: None
W1282X, del articulo 35624092 detectado con Prob: None
W1282X, del articulo 35624092 detectado con Prob: None
W1282X, del articulo 35624092 detectado con Prob: None
1
Homo sapiens

 {'Organismo': 'Mus musculus', 'Articulos': ['35668939', '35660026', '35635440', '

In [238]:
dataFinal

StartNode  \
0                                                   agi/   
1                                                   agi/   
2                                                   agi/   
3                                                   agi/   
4                                                   agi/   
5                                                   agi/   
6                                                   agi/   
7                                                   agi/   
8                                                   agi/   
9                                                   agi/   
10                                                  agi/   
11                                                  agi/   
12                                                  agi/   
13                                                  agi/   
14                                                  agi/   
15                                                  agi/   
16                                                  agi/   
17                                                  agi/   
18                                                  agi/   
19                                                  agi/   
20                                                  agi/   
21                                                  agi/   
22                                                  agi/   
23                                                  agi/   
24                                                  agi/   
25                                                  agi/   
26                                                  agi/   
27                                             agi/ii of   
28                                             agi/ii of   
29                                             agi/ii of   
30                                             agi/ii of   
31                                             agi/ii of   
32                                             agi/ii of   
33                                             agi/ii of   
34                                             agi/ii of   
35                                             agi/ii of   
36                                             agi/ii of   
37                                             agi/ii of   
38                                             agi/ii of   
39                                             agi/ii of   
40                                             agi/ii of   
41                                             agi/ii of   
42                                             agi/ii of   
43                                             agi/ii of   
44                                             agi/ii of   
45                                             agi/ii of   
46                                             agi/ii of   
47                                             agi/ii of   
48                                             agi/ii of   
49                                             agi/ii of   
50                                             agi/ii of   
51                                             agi/ii of   
52                                             agi/ii of   
53                                             agi/ii of   
54                          airway epithelial cell lines   
55                          airway epithelial cell lines   
56                          airway epithelial cell lines   
57                          airway epithelial cell lines   
58                          airway epithelial cell lines   
59                          airway epithelial cell lines   
60                          airway epithelial cell lines   
61                          airway epithelial cell lines   
62                          airway epithelial cell lines   
63                          airway epithelial cell lines   
64                          airway epithelial cell lines   
65                          airway epithelial cell lines   
66                         

In [239]:
dataFinal.to_csv('node_structure.csv', sep=';', encoding='utf-8')